# 1. Knowledge Graphs - Data Preprocessing

## 1.1. Load Data

In [2]:
import pandas as pd

In [3]:
# import movie plots from: https://www.kaggle.com/jrobischon/wikipedia-movie-plots/
movie_plots_data = pd.read_csv('wiki_movie_plots_deduped.csv')

In [4]:
print(movie_plots_data.shape)

(34886, 8)


## 1.2. Select Subset

In [5]:
movie_plots_data_selection = movie_plots_data[movie_plots_data['Release Year'] >= 2005]

In [7]:
plots = movie_plots_data_selection.Plot

In [8]:
plots.head()

14591    Andy Stitzer is a 40-year-old virgin who lives...
14592    51 Birch Street is the first-person account of...
14593    Max is a lonely child in the suburbs of Austin...
14594    In 2011, a deadly pathogenic virus has killed ...
14595    In 1974, Ronald DeFeo Jr. murdered his family ...
Name: Plot, dtype: object

## 1.3. Split Movie Plots Into Phrases

In [9]:
phrases = []
for plot in plots.head(1000):
    phrases_all = plot.split('.')
    phrases_filtered = [p.strip() for p in phrases_all if p.strip() and len(p.strip()) > 3]
    phrases += phrases_filtered

In [10]:
from textacy.extract import subject_verb_object_triples

In [11]:
import spacy
nlp = spacy.load('en_core_web_sm')

In [12]:
doc = nlp('They are watching a movie')
iterator = subject_verb_object_triples(doc)
for it in iterator:
    print(it)

(They, are watching, movie)


## 1.4. Extract SVO Triples

In [13]:
from tqdm import tqdm

In [14]:
triples_raw = []

for p in tqdm(phrases):
    iterator = subject_verb_object_triples(nlp(p))
    phrase_triples = []
    for svo in iterator:
        phrase_triples.append(svo)
    triples_raw.append(phrase_triples)

100%|██████████| 28127/28127 [07:08<00:00, 65.65it/s]


## 1.5. Lemmatize & Stem SVO Triples

In [15]:
from nltk.stem import WordNetLemmatizer, SnowballStemmer
from nltk.corpus.reader.wordnet import VERB

In [17]:
lemmatizer = WordNetLemmatizer()

In [18]:
lemmatized_triples = []
lemmatized_stemmed_triples = []

In [19]:
stemmer = SnowballStemmer('english')

In [20]:
def lemmatize_stem(text):
    # lemmatize + stem a text
    return stemmer.stem(WordNetLemmatizer().lemmatize(text))

In [21]:
phrase_counter = 0
found_triples_counter = 0

In [24]:
for (phrase, phrase_triples) in zip(phrases, triples_raw):
    print('phrase triples:', phrase_triples)
    if len(phrase) > 0:
        phrase_counter += 1
    if phrase_triples:
        found_triples_counter += 1
        for triple in phrase_triples:
            print('raw triples:', triple)
            # lemmatize
            s = lemmatizer.lemmatize(str(triple[0]))
            o = lemmatizer.lemmatize(str(triple[2]))
            v = lemmatizer.lemmatize(str(triple[1][-1]), VERB)  # take last token in verb expression
            
            # lemmatize & stem
            lss = lemmatize_stem(str(triple[0]))
            lso = lemmatize_stem(str(triple[2]))
            lsv = lemmatize_stem(str(triple[1][-1]))
            
            print('lemmatized: s:', s, ', o:', o, ', v:', v)
            print('lemmatized&stemmed: s:', lss, ', o:', lso, ', v:', lsv)
            
            lemmatized_triples.append([s.lower(), v.lower(), o.lower()])
            lemmatized_stemmed_triples.append([lss.lower(), lsv.lower(), lso.lower()])
    else:
        print('Could not detect triples in phrase:', phrase)
        lemmatized_triples.append([])
        lemmatized_stemmed_triples.append([])

phrase triples: []
Could not detect triples in phrase: Andy Stitzer is a 40-year-old virgin who lives alone, his apartment filled with his collection of action figures and video games
phrase triples: [(conversation, turns, past), (him, lose, virginity)]
raw triples: (conversation, turns, past)
lemmatized: s: conversation , o: past , v: turn
lemmatized&stemmed: s: convers , o: past , v: turn
raw triples: (him, lose, virginity)
lemmatized: s: him , o: virginity , v: lose
lemmatized&stemmed: s: him , o: virgin , v: lose
phrase triples: [(men, give, Andy), (men, give, advice)]
raw triples: (men, give, Andy)
lemmatized: s: men , o: Andy , v: give
lemmatized&stemmed: s: men , o: andi , v: give
raw triples: (men, give, advice)
lemmatized: s: men , o: advice , v: give
lemmatized&stemmed: s: men , o: advic , v: give
phrase triples: [(Cal, advises, ask), (Andy, ask, questions)]
raw triples: (Cal, advises, ask)
lemmatized: s: Cal , o: ask , v: advise
lemmatized&stemmed: s: cal , o: ask , v: advis

phrase triples: [(Max, informs, class), (Planet Drool, became, dreamworld), (Sharkboy, became, King), (Lavagirl, became, Queen), (Max, finishing, Tobor), (he, reminds, class), (he, reminds, dream), (he, reminds, work)]
raw triples: (Max, informs, class)
lemmatized: s: Max , o: class , v: inform
lemmatized&stemmed: s: max , o: class , v: inform
raw triples: (Planet Drool, became, dreamworld)
lemmatized: s: Planet Drool , o: dreamworld , v: become
lemmatized&stemmed: s: planet drool , o: dreamworld , v: becam
raw triples: (Sharkboy, became, King)
lemmatized: s: Sharkboy , o: King , v: become
lemmatized&stemmed: s: sharkboy , o: king , v: becam
raw triples: (Lavagirl, became, Queen)
lemmatized: s: Lavagirl , o: Queen , v: become
lemmatized&stemmed: s: lavagirl , o: queen , v: becam
raw triples: (Max, finishing, Tobor)
lemmatized: s: Max , o: Tobor , v: finish
lemmatized&stemmed: s: max , o: tobor , v: finish
raw triples: (he, reminds, class)
lemmatized: s: he , o: class , v: remind
lemmat

lemmatized: s: kid , o: him , v: attack
lemmatized&stemmed: s: kid , o: him , v: attack
phrase triples: []
Could not detect triples in phrase: During the fight, Kevin has an asthma attack and collapses
phrase triples: []
Could not detect triples in phrase: Nick rushes to his aid and revives him
phrase triples: []
Could not detect triples in phrase: Witnessing the event, Suzanne believes trusting Nick was a mistake
phrase triples: []
Could not detect triples in phrase: After encouragement from Satchel, Nick goes to Suzanne's hotel to tell her and the kids farewell for good
phrase triples: [(Nick, have grown, to care), (kids, have grown, to care)]
raw triples: (Nick, have grown, to care)
lemmatized: s: Nick , o: to care , v: grow
lemmatized&stemmed: s: nick , o: to car , v: grown
raw triples: (kids, have grown, to care)
lemmatized: s: kid , o: to care , v: grow
lemmatized&stemmed: s: kid , o: to car , v: grown
phrase triples: []
Could not detect triples in phrase: Detroit Police Departme

lemmatized: s: Bruce , o: to travel , v: decide
lemmatized&stemmed: s: bruce , o: to travel , v: decid
raw triples: (Bruce, decides, learn)
lemmatized: s: Bruce , o: learn , v: decide
lemmatized&stemmed: s: bruce , o: learn , v: decid
phrase triples: [(he, meets, Ducard), (who, trains, him)]
raw triples: (he, meets, Ducard)
lemmatized: s: he , o: Ducard , v: meet
lemmatized&stemmed: s: he , o: ducard , v: meet
raw triples: (who, trains, him)
lemmatized: s: who , o: him , v: train
lemmatized&stemmed: s: who , o: him , v: train
phrase triples: [(League, intends, to destroy)]
raw triples: (League, intends, to destroy)
lemmatized: s: League , o: to destroy , v: intend
lemmatized&stemmed: s: leagu , o: to destroy , v: intend
phrase triples: [(Bruce, rejects, cause)]
raw triples: (Bruce, rejects, cause)
lemmatized: s: Bruce , o: cause , v: reject
lemmatized&stemmed: s: bruce , o: caus , v: reject
phrase triples: [(Bruce, saves, Ducard)]
raw triples: (Bruce, saves, Ducard)
lemmatized: s: Bruc

lemmatized: s: Edie , o: award ceremony , v: leave
lemmatized&stemmed: s: edi , o: award ceremoni , v: leav
raw triples: (Chili, leave, award ceremony)
lemmatized: s: Chili , o: award ceremony , v: leave
lemmatized&stemmed: s: chili , o: award ceremoni , v: leav
phrase triples: [(he, passes, billboard)]
raw triples: (he, passes, billboard)
lemmatized: s: he , o: billboard , v: pass
lemmatized&stemmed: s: he , o: billboard , v: pass
phrase triples: [(daughter, can attend, music school)]
raw triples: (daughter, can attend, music school)
lemmatized: s: daughter , o: music school , v: attend
lemmatized&stemmed: s: daughter , o: music school , v: attend
phrase triples: [(She, 's made, name), (She, 's made, for)]
raw triples: (She, 's made, name)
lemmatized: s: She , o: name , v: make
lemmatized&stemmed: s: she , o: name , v: made
raw triples: (She, 's made, for)
lemmatized: s: She , o: for , v: make
lemmatized&stemmed: s: she , o: for , v: made
phrase triples: [(people, finds, herself), (tr

...

lemmatized: s: he , o: himself , v: find
lemmatized&stemmed: s: he , o: himself , v: find
phrase triples: [(Eliot, tells, him), (he, never made, it), (which, killed, him)]
raw triples: (Eliot, tells, him)
lemmatized: s: Eliot , o: him , v: tell
lemmatized&stemmed: s: eliot , o: him , v: tell
raw triples: (he, never made, it)
lemmatized: s: he , o: it , v: make
lemmatized&stemmed: s: he , o: it , v: made
raw triples: (which, killed, him)
lemmatized: s: which , o: him , v: kill
lemmatized&stemmed: s: which , o: him , v: kill
phrase triples: [(Eliot, inserts, trocar)]
raw triples: (Eliot, inserts, trocar)
lemmatized: s: Eliot , o: trocar , v: insert
lemmatized&stemmed: s: eliot , o: trocar , v: insert
phrase triples: []
Could not detect triples in phrase: The story begins in 1957 in the star-filled skies above California's Mojave Desert
phrase triples: [(who, is preparing, anniversary dinner)]
raw triples: (who, is preparing, anniversary dinner)
lemmatized: s: who , o: anniversary dinner 

lemmatized&stemmed: s: steve , o: to real , v: begin
phrase triples: [(who, is made, to feel)]
raw triples: (who, is made, to feel)
lemmatized: s: who , o: to feel , v: make
lemmatized&stemmed: s: who , o: to feel , v: made
phrase triples: [(Hartman, take, credit)]
raw triples: (Hartman, take, credit)
lemmatized: s: Hartman , o: credit , v: take
lemmatized&stemmed: s: hartman , o: credit , v: take
phrase triples: []
Could not detect triples in phrase: Mary finally realizes she does not need Steve to be happy
phrase triples: [(you, love, someone)]
raw triples: (you, love, someone)
lemmatized: s: you , o: someone , v: love
lemmatized&stemmed: s: you , o: someon , v: love
phrase triples: [(Hartman, got, popularity)]
raw triples: (Hartman, got, popularity)
lemmatized: s: Hartman , o: popularity , v: get
lemmatized&stemmed: s: hartman , o: popular , v: got
phrase triples: []
Could not detect triples in phrase: During a benefit concert in Paris, France, David Seville is injured from a backst

Could not detect triples in phrase: Peter's Tomb below the church, but the battery life is too low to risk re-connecting it to a battery
phrase triples: [(McKenna, seizes, vial)]
raw triples: (McKenna, seizes, vial)
lemmatized: s: McKenna , o: vial , v: seize
lemmatized&stemmed: s: mckenna , o: vial , v: seiz
phrase triples: []
Could not detect triples in phrase: At a high altitude, he parachutes out as the antimatter bomb explodes overhead
phrase triples: [(McKenna, is hailed, hero), (McKenna, is hailed, savior)]
raw triples: (McKenna, is hailed, hero)
lemmatized: s: McKenna , o: hero , v: hail
lemmatized&stemmed: s: mckenna , o: hero , v: hail
raw triples: (McKenna, is hailed, savior)
lemmatized: s: McKenna , o: savior , v: hail
lemmatized&stemmed: s: mckenna , o: savior , v: hail
phrase triples: [(Langdon, use, key), (Langdon, use, to watch), (Vetra, use, key), (Vetra, use, to watch)]
raw triples: (Langdon, use, key)
lemmatized: s: Langdon , o: key , v: use
lemmatized&stemmed: s: la

lemmatized: s: they , o: Toby , v: give
lemmatized&stemmed: s: they , o: tobi , v: give
raw triples: (they, give, name)
lemmatized: s: they , o: name , v: give
lemmatized&stemmed: s: they , o: name , v: give
phrase triples: []
Could not detect triples in phrase: Astro departs with the kids, finding people still live on the Surface
phrase triples: [(who, runs, fighting ring)]
raw triples: (who, runs, fighting ring)
lemmatized: s: who , o: fighting ring , v: run
lemmatized&stemmed: s: who , o: fighting r , v: run
phrase triples: []
Could not detect triples in phrase: The next day, Astro comes across an offline construction robot Zog, whom he revives with the Blue Core's energy
phrase triples: [(Hamegg, scans, Astro)]
raw triples: (Hamegg, scans, Astro)
lemmatized: s: Hamegg , o: Astro , v: scan
lemmatized&stemmed: s: hamegg , o: astro , v: scan
phrase triples: [(Astro, defeats, fighters), (robots, refuse, to fight)]
raw triples: (Astro, defeats, fighters)
lemmatized: s: Astro , o: fighte

lemmatized&stemmed: s: he , o: person , v: convinc
phrase triples: [(they, share, drugs)]
raw triples: (they, share, drugs)
lemmatized: s: they , o: drug , v: share
lemmatized&stemmed: s: they , o: drug , v: share
phrase triples: [(He, become, alcoholic), (He, become, stepmother), (who, bring, himself)]
raw triples: (He, become, alcoholic)
lemmatized: s: He , o: alcoholic , v: become
lemmatized&stemmed: s: he , o: alcohol , v: becom
raw triples: (He, become, stepmother)
lemmatized: s: He , o: stepmother , v: become
lemmatized&stemmed: s: he , o: stepmoth , v: becom
raw triples: (who, bring, himself)
lemmatized: s: who , o: himself , v: bring
lemmatized&stemmed: s: who , o: himself , v: bring
phrase triples: [(he, uses, position), (he, uses, bully), (he, uses, steal)]
raw triples: (he, uses, position)
lemmatized: s: he , o: position , v: use
lemmatized&stemmed: s: he , o: posit , v: us
raw triples: (he, uses, bully)
lemmatized: s: he , o: bully , v: use
lemmatized&stemmed: s: he , o: bu

In [ ]:
print('Triples Detection Rate:', (found_triples_counter / phrase_c))